<a href="https://colab.research.google.com/github/nspll/Final_project/blob/master/finding_answer.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#สกัดคำตอบ

ใช้ cosinerelevant 

In [0]:
!pip install pythainlp
from pythainlp.tokenize import word_tokenize
from pythainlp.corpus import stopwords
from pythainlp import word_vector 
from gensim.models import Word2Vec

import numpy as np

words = stopwords.words('thai')

In [0]:
def qa_fruit_demo(question,paragraph,set_d_nb):
  '''
  (str,str,int) => dict
  
  params:
  question : string of question
  paragraph : string of paragraph content of each article
  set_d_nb : window size 
  '''
  q_token = word_tokenize(question,engine= "deepcut") #question_token = ['เฮโจเกียว','หรือ','เฮเซเกียว','เป็น','เมือง','หลวง','ของ','ประเทศ','ใด']
  p_token = word_tokenize(paragraph,engine= "deepcut")
 
  all_pos = keyword_n_position(p_token , q_token)
  p_model = Word2Vec([p_token],min_count=1)
  q_model = Word2Vec([q_token],min_count=1)
  np_pos = []
  
  for i in all_pos[1]:
 
    for d_nb in range(set_d_nb):
        np_pos.append(i+d_nb)
        np_pos.append(i-d_nb)

  my_np_pos =  [pos for pos in np_pos if pos>=0 and pos<len(p_token)]
  '''
  #check bug
  print ('p_tpken',p_token)
  print ('q_token',q_token)
  print ('all_pos',all_pos)
  print('set_d_nb',set_d_nb)
  print('my_np_pos',my_np_pos)
  print ('np_pos',np_pos)
  '''
  p = np.array(all_pos[1])
  treshold = p.sum()/len(p)+ p.std()
  relavent_score_list = []
  #relavent = [(candidate,score)]
  for candidate in list(set(my_np_pos)): #position in paragraph
    
      rs = 0 
      #print ("candidate" ,candidate)
      for neighbor in all_pos[1]:
        if neighbor < treshold :
            #ค่า cosine similarity ของคำที่น่าจะเป็นคำตอบในพารากราฟเทียบกับทุกคำในคำถาม
            rs = cosine_relevant_score(p_token[candidate],q_token,p_model,q_model)
      relavent_score_list.append((candidate,rs))
  #print ("find_max",find_max(relavent_score)) #change to find most similarity
  answer = p_token[find_max(relavent_score_list)]
  choice_answer = []
 
  relavent_score_sorted = sorted(relavent_score_list,key=lambda x: x[1],reverse = True)[:]
  #print ("find_max",find_max(relavent_score_list),"answer",p_token[find_max(relavent_score_list)])
  #print( relavent_score_sorted)
  for a in relavent_score_sorted:
     choice_answer.append(p_token[a[0]])
  
  #print ("choice_answer= ",choice_answer)
  #print ("cut answer = ",cut_ans(choice_answer,q_token))
  return { 'choice_answer':set(cut_ans(choice_answer,q_token)),'candidate':list(set(my_np_pos)),'neighbor': all_pos[1],'neighbor_w_words': all_pos[0]}  


def keyword_n_position(p_token,q_token):
  '''
  (list,list) => (dictionary,)
  return tuple of
  '''
  nb = {}
  tk_list = []
  pos_list = []
  i = 0
  for tkn in p_token:
    if tkn in q_token and tkn not in tk_list:
      if i == 0:
        print (tkn,i)
      tk_list.append(tkn)
      pos_list.append(i)
      nb[tkn] = [i]
    elif tkn in q_token and tkn in  tk_list:
      nb[tkn].append(i)
      pos_list.append(i)
    i = i + 1 
  return (nb,pos_list)

def find_max(rs):
  m_max = 0
  i_max = 0
  for i in rs:
    if i[1] >= m_max:
      i_max = i
      m_max = i[1]
  return i_max[0]

def cut_ans(ans_tkn,q_token):
  return [i for i in ans_tkn if i not in q_token and i not in ' "()\/.,' and  i not in words]

def cosine_relevant_score(p_token,q_token_list,pmodel,qmodel):
  cosine_similarity = 0
  for q_token in q_token_list:
    cosine_similarity += np.dot(pmodel[p_token], qmodel[q_token])
  return cosine_similarity 


ทดสอบจากข้อมูล 100 ชุดของ nsc

In [0]:
from google.colab import drive
drive.mount('/content/drive')

In [0]:
import pandas as pd
f = pd.DataFrame(file).to_csv("/content/drive/Team Drives/pre-snporject/result/hiii.csv")

',0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48,49,50,51,52,53,54,55,56,57,58,59,60,61,62,63,64,65,66,67,68,69,70,71,72,73,74,75,76,77,78,79,80,81,82,83,84,85,86,87,88,89,90,91,92,93,94,95,96,97,98,99\n0,"{\'question_id\': 1, \'question\': \'เอเลียนส์เป็นภาพยนตร์แนวไหน\', \'answer\': \'นิยายวิทยาศาสตร์แอคชั่น\', \'answer_begin_position \': 149, \'answer_end_position\': 172, \'article_id\': 473065, \'content\': \'<doc id=""473065"" url=""https://th.wikipedia.org/wiki?curid=473065"" title=""เอเลี่ยน 2 ฝูงมฤตยูนอกโลก"">เอเลี่ยน 2 ฝูงมฤตยูนอกโลก เอเลียนส์ เป็นภาพยนตร์นิยายวิทยาศาสตร์แอคชั่นในปี ค.ศ. 1986 กำกับการแสดงโดย เจมส์ แคเมรอน และนำแสดงโดย Sigourney Weaver ,Carrie Henn ,Michael Biehn ,Lance Henriksen ,William Hope และPaul Reiser เป็นภาคต่อจากภาพยนตร์ปี ค.ศ. 1979 เอเลียน สร้างโดยทเวนตีท์เซนจูรีฟอกซ์</doc>\\n\', \'result\': {\'choice_answer\': [\'นิยาย\', \'ปี\', \'วิทยาศาสตร์แอคชั่น\', \'Reiser

In [0]:
import json
path = '/content/drive/Team Drives/pre-snporject/result/nsc_result_fruit_cosine'
file = [json.loads(i) for i in open(path,'r',encoding = 'utf-8').readlines()]
def collect_answer(dic):
  for i in dic[0] :
    print (i['question'])
    print (i['result'])
    print (i['answer'])
    i['position_answer'] = input('ตำแหน่งที่ถูก')
  return dic 
collect_answer(file)
print ("finish will save file")
save_file = open('/content/drive/Team Drives/pre-snporject/result/nsc_result_fruit_cosine_with_correct_position','w',encoding = 'urf-8')

เอเลียนส์เป็นภาพยนตร์แนวไหน
{'choice_answer': ['นิยาย', 'ปี', 'วิทยาศาสตร์แอคชั่น', 'Reiser', 'โลก'], 'candidate': [32, 33, 34, 35, 76, 77, 78, 79, 80, 81, 82, 83, 84, 28, 29, 30, 31], 'neighbor': [30, 32, 33, 78, 82]}
นิยายวิทยาศาสตร์แอคชั่น
พระเจ้าอาฟองโซที่ 1 แห่งโปรตุเกส เป็นผู้สืบเชื้อสายจากราชวงศ์ใด
{'choice_answer': ['พรรษา', 'พรรษา', 'พรรษา', 'พรรษา', 'พระราชสมภพ', 'พระราชสมภพ', 'เสด็จ', 'เสด็จ', 'เสด็จ', 'พระชนมายุ', 'พระชนมายุ', '>', 'พระนัดดา', 'สวรรค', 'เทเรซา เคาน์เตส', '76', 'ดยุก', 'กษัตริย์', '30', '30', '=', 'ปี', 'ปี', '3', 'พระราชประวัติ', 'พระราชประวัติ', 'ธันวาคม', 'url=', 'ช่วยเหลือ', 'ราชวงศ์กาเป', 'สเปน', '1139', '1139', '1112', 'เตียง', 'ปกครอง', 'พระองค์', 'พระองค์', '289367', '289367', '25', 'เคานต์', 'เคานต์', 'เคานต์', 'ครอง', 'ครอง', 'ครอง', 'สวรรคต', 'สวรรคต', 'รอแบร์', 'ค.ศ.', 'ค.ศ.', 'ค.ศ.', 'ค.ศ.', 'ค.ศ.', 'title', '26', 'ราชย์', 'ราชย์', 'เอนรีกี', 'ปฐมกษัตริย์', 'เศษ', 'พระโอรส', 'ต', 'แคว้นโปรตุเกส', '1185', 'พระราชบิดา', 'พระราชบิดา', 'คาสตีล', 'บู

KeyboardInterrupt: ignored

In [0]:
import json
nsc_path = "/content/drive/Team Drives/pre-snporject/data/nsc_100_data/"
nsc_qa_json = open('/content/drive/Team Drives/pre-snporject/data/test_data_nsc_100qa_json','r',encoding='utf-8')
nsc_qa  = [json.loads(i) for i in nsc_qa_json.readlines()][0]
print(nsc_qa)
 

[{'question_id': 1, 'question': 'เอเลียนส์เป็นภาพยนตร์แนวไหน', 'answer': 'นิยายวิทยาศาสตร์แอคชั่น', 'answer_begin_position ': 149, 'answer_end_position': 172, 'article_id': 473065}, {'question_id': 2, 'question': 'พระเจ้าอาฟองโซที่ 1 แห่งโปรตุเกส เป็นผู้สืบเชื้อสายจากราชวงศ์ใด', 'answer': 'ราชวงศ์กาเปเตียง', 'answer_begin_position ': 218, 'answer_end_position': 234, 'article_id': 289367}, {'question_id': 3, 'question': 'เฝิง เส้าเฟิง รับบทอะไรใน The Palace', 'answer': 'องค์ชาย 8', 'answer_begin_position ': 362, 'answer_end_position': 371, 'article_id': 639294}, {'question_id': 4, 'question': 'หม่อมราชวงศ์กุลปราโมทย์ จิรประวัติ ราชสกุลเดิมคืออะไร', 'answer': 'สวัสดิกุล', 'answer_begin_position ': 194, 'answer_end_position': 203, 'article_id': 619806}, {'question_id': 5, 'question': 'ชิงชัน เป็นพืชชนิดใด', 'answer': 'ไม้ยืนต้น', 'answer_begin_position ': 107, 'answer_end_position': 116, 'article_id': 135329}, {'question_id': 6, 'question': 'แฝดไข่ร่วมคืออะไร', 'answer': 'ลูกทั้งสองเจริญม

In [0]:
for i in nsc_qa :
  data_content = open(nsc_path+str(i['article_id'])+".txt",'r',encoding='utf-8').read()
  result = qa_fruit_demo(i['question'],data_content,3)
  i['content'] = data_content
  i['result'] = result
  print(i['question'],i['result'])
  print("===================================================================================")
  
  

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:93: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).


เอเลียนส์เป็นภาพยนตร์แนวไหน {'choice_answer': ['นิยาย', 'ปี', 'วิทยาศาสตร์แอคชั่น', 'Reiser', 'โลก'], 'candidate': [32, 33, 34, 35, 76, 77, 78, 79, 80, 81, 82, 83, 84, 28, 29, 30, 31], 'neighbor': [30, 32, 33, 78, 82]}
พระเจ้าอาฟองโซที่ 1 แห่งโปรตุเกส เป็นผู้สืบเชื้อสายจากราชวงศ์ใด {'choice_answer': ['พรรษา', 'พรรษา', 'พรรษา', 'พรรษา', 'พระราชสมภพ', 'พระราชสมภพ', 'เสด็จ', 'เสด็จ', 'เสด็จ', 'พระชนมายุ', 'พระชนมายุ', '>', 'พระนัดดา', 'สวรรค', 'เทเรซา เคาน์เตส', '76', 'ดยุก', 'กษัตริย์', '30', '30', '=', 'ปี', 'ปี', '3', 'พระราชประวัติ', 'พระราชประวัติ', 'ธันวาคม', 'url=', 'ช่วยเหลือ', 'ราชวงศ์กาเป', 'สเปน', '1139', '1139', '1112', 'เตียง', 'ปกครอง', 'พระองค์', 'พระองค์', '289367', '289367', '25', 'เคานต์', 'เคานต์', 'เคานต์', 'ครอง', 'ครอง', 'ครอง', 'สวรรคต', 'สวรรคต', 'รอแบร์', 'ค.ศ.', 'ค.ศ.', 'ค.ศ.', 'ค.ศ.', 'ค.ศ.', 'title', '26', 'ราชย์', 'ราชย์', 'เอนรีกี', 'ปฐมกษัตริย์', 'เศษ', 'พระโอรส', 'ต', 'แคว้นโปรตุเกส', '1185', 'พระราชบิดา', 'พระราชบิดา', 'คาสตีล', 'บูร์กอญ', 'กรกฎาคม', 'กรกฎ

In [0]:
open("nsc_result",'w',encoding='utf-8').write(json.dumps(nsc_qa))

3025884

#wikidumps

ทดสอบกับคำถาม 156 คำถามที่ตั้งเอง โดยส่วนมากเป็นลักษณะคำถามที่ลงท้ายด้วย ''อะไร" ,"เมื่อใด" 

In [0]:
from google.colab import drive
drive.mount('/content/drive/')

Drive already mounted at /content/drive/; to attempt to forcibly remount, call drive.mount("/content/drive/", force_remount=True).


In [0]:
import json
path = '/content/drive/Team Drives/pre-snporject/data/sample_data/'
wiki_01 = [json.loads(line) for line in open(path+"wiki_01.txt",'r',encoding='utf-8').readlines()]

In [0]:
len(wiki_00)

57

In [0]:
wiki_01.extend(wiki_00)

In [0]:
len(wiki_01)

156

In [0]:
open(path+"wikidump_156_article_from_wiki00_wiki01",'x',encoding='utf-8').write(json.dumps(wiki_01))

FileExistsError: ignored

In [0]:
path2 = '/content/drive/Team Drives/pre-snporject/data/sample_question/'
mytest58 = [json.loads(line) for line in open(path2+"mytest_58qa_json",'r',encoding='utf-8').readlines()]

In [0]:
len(mytest60[0][0])

7

In [0]:
test_dump_data2 = []

In [0]:

for i in mytest60[0]:
  if len(i) == 7 :
    j = j+1
    i['question_id'] = 100+j
    test_dump_data.append(i)
print (j)

117


In [0]:
k = 0
for i in mytest58[0].extend(mytest60[0]):
  if len(i) == 7 and i['question'] != '' :
    k = k+1
    i['question_id'] = 100+k
    test_dump_data2.append(i)
  
print (36 , len(mytest60[0]),len(mytest58[0]),k)

36 99 57 34


In [0]:
test_dump_data[116]

{'correct_paragraph': '1',
 'id': '1646',
 'question': 'คนเก่งทะลุโลก หรือ คนเก่งฟ้าประทาน แปลตรงตัวว่าอะไร',
 'question_id': 217,
 'text': ['คนเก่งทะลุโลก',
  'คนเก่งทะลุโลก หรือ คนเก่งฟ้าประทาน () แปลตรงตัวว่า "สมุดปกขาวเรื่องผี" เป็นการ์ตูนญี่ปุ่น ผลงานของ โยชิฮิโร โตกาชิ จัดพิมพ์โดย สำนักพิมพ์สยามอินเตอร์คอมิกส์ ได้รับการสร้างเป็นอะนิเมะและวิดีโอเกม เคยออกอากาศทางช่อง 9 อ.ส.ม.ท. (หรือ โมเดิร์นไนน์ทีวี ในปัจจุบัน) ในช่วงช่อง 9 การ์ตูน (หรือ โมเดิร์นไนน์การ์ตูน ในปัจจุบัน) ในปี พ.ศ. 2541',
  'เป็นเรื่องราวเกี่ยวกับเด็กหนุ่มจอมเกเร อุราเมชิ ยูสึเกะ จากการเข้าไปช่วยเด็กน้อยให้พ้นจากอุบัติเหตุกลับทำให้เขาต้องเสียชีวิตแทนด้วยความดีนี้ทำให้โลกวิญญาณให้โอกาสเขาฟื้นคืนชีพได้ (เป็นกรณีพิเศษร้อยปีมีครั้ง เพราะยูสึเกะทำไปโดยไร้ความคิด) และมีชีวิตอยู่ในฐานะของ "นักสืบโลกวิญญาณ" คอยจัดการกับเรื่องราวที่เกี่ยวกับวิญญาณและปิศาจต่าง ๆ ที่เกิดขึ้นในโลกมนุษย์',
  'ยูสึเกะและพรรคพวกได้รับเชิญให้เข้าร่วมงานประลองที่จัดขึ้นบนเกาะห่างไกล เป็นเวทีต่อสู้อันโหดเหี้ยมของปิศาจที่มีเบื้องหลังคือมนุษย์ผู้ละโมบ 

In [0]:
open(path2+"wikidump_117qa_json_from_wiki00_wiki01",'x',encoding='utf-8').write(json.dumps(test_dump_data))

3311054

ลอง ด้านบนทำการเตรียมดาต้าเฉยๆ เนื่องจาก มี format ต่างจากตัว nsc

In [0]:
qa_path = '/content/drive/Team Drives/pre-snporject/data/sample_question/wikidump_117qa_json_from_wiki00_wiki01'
dumps_117_qa =  [json.loads(line) for line in open(qa_path,'r',encoding='utf-8').readlines()]

In [0]:
len(dumps_117_qa[0])

117

In [0]:
dumps_117_qa[0][49]


{'correct_paragraph': 1,
 'id': '798',
 'question': 'รายชื่อหนังสือดี 100 เล่ม ที่คนไทยควรอ่าน (พ.ศ. 2408-2519) เป็นงานวิจัยของใคร',
 'question_id': 151,
 'text': ['หนังสือดี 100 เล่มที่คนไทยควรอ่าน',
  'รายชื่อหนังสือดี 100 เล่ม ที่คนไทยควรอ่าน (พ.ศ. 2408-2519) เป็นงานวิจัยของวิทยากร เชียงกูล ผู้อำนวยการศูนย์วิจัยสังคมศาสตร์ มหาวิทยาลัยรังสิต ร่วมกับคณะวิจัยอีก 10 ท่าน ชื่อ "โครงการวิจัยเพื่อคัดเลือกและแนะนำหนังสือดีในรอบศตวรรษ" ซึ่งได้รับการสนับสนุนจากสำนักงานกองทุนสนับสนุนการวิจัย (สกว.) ในช่วงปี พ.ศ. 2540-2541'],
 'title': 'หนังสือดี 100 เล่มที่คนไทยควรอ่าน',
 'url': 'https://th.wikipedia.org/wiki?curid=798'}

In [0]:
def read_edit(i):
  if dumps_117_qa[0][i]['question'] == '':
        print (dumps_117_qa[0][i]['text'])
        dumps_117_qa[0][i]['question'] = input("question")
        dumps_117_qa[0][i]['correct_paragraph'] = input("paragraph")

In [0]:
for c in range(116):
  read_edit(c)

['OS', 'OS, Os อาจหมายถึง']
question
paragraph
['88 หนังสือดีวิทยาศาสตร์ไทย', '88 หนังสือดีวิทยาศาสตร์ เป็นผลการวิจัยของคณะวิจัย โครงการวิจัยหนังสือดีวิทยาศาสตร์ ภายใต้การสนับสนุนของ สำนักงานกองทุนสนับสนุนการวิจัย (สกว.) และกรมวิชาการ โดยคณะวิจัยของโครงการได้ทำการคัดเลือกหนังสือซึ่งมีเนื้อหาเกี่ยวกับวิทยาศาสตร์ ที่ตีพิมพ์เป็นเล่ม เนื้อหาเกี่ยวกับวิทยาศาสตร์ ที่เป็นภาษาไทย เขียนโดยชาวไทย ตั้งแต่ ยุคสุโขทัย ถึง พ.ศ. 2536 มากกว่า 500 เล่ม แล้วแถลงข่าวประกาศยกย่องเมื่อ 28 มีนาคม พ.ศ. 2544', 'ในจำนวนหนังสือ 88 เล่มนี้ สามารถแบ่งออกได้เป็น 3 ประเภท คือ']
question88 หนังสือดีวิทยาศาสตร์  ได้รับการสนันสนุนจากองค์กรใด
paragraph1
['สถาบันเทคโนโลยีแห่งเอเชีย', 'สถาบันเทคโนโลยีแห่งเอเชีย () หรือ เอไอที เป็นสถาบันการศึกษาที่มีสถานะเป็นองค์การระหว่างประเทศ ก่อตั้งเมื่อ พ.ศ. 2502 โดยความร่วมมือจากกลุ่มประเทศสนธิสัญญาป้องกันภูมิภาคเอเชียตะวันออกเฉียงใต้ (ซีโต้ หรือ สปอ.) ในชื่อ โรงเรียนวิศวกรรม สปอ. (SEATO Graduate School of Engineering) ก่อนจะเปลี่ยนมาเป็นสถาบันอิสระในชื่อปัจจุบันเมื่อเดือนพฤศจิกายน 

In [0]:
cnt = 0
for i in dumps_117_qa[0]:
  if len(i['question']) < 2:
    cnt = cnt+1
    print(i)
    dumps_117_qa[0].remove(i)
print(cnt)

{'title': 'เหนือพระเจ้า', 'url': 'https://th.wikipedia.org/wiki?curid=894', 'id': '894', 'text': ['เหนือพระเจ้า', 'เหนือพระเจ้า', '<br clear="all">'], 'question': '', 'correct_paragraph': '', 'question_id': 171}
{'title': 'ประเทศไทย', 'url': 'https://th.wikipedia.org/wiki?curid=936', 'id': '936', 'text': ['ประเทศไทย', 'ประเทศไทย มีชื่ออย่างเป็นทางราชการว่า ราชอาณาจักรไทย เป็นรัฐชาติอันตั้งอยู่ในภูมิภาคเอเชียตะวันออกเฉียงใต้ เดิมมีชื่อว่า "สยาม" รัฐบาลประกาศเปลี่ยนชื่อเป็นประเทศไทยอย่างเป็นทางการตั้งแต่ปี 2482 ประเทศไทยมีขนาดใหญ่เป็นอันดับที่ 50 ของโลก มีเนื้อที่ 513,120 ตารางกิโลเมตร และมีประชากรมากเป็นอันดับที่ 20 ของโลก คือ ประมาณ 68 ล้านคน กรุงเทพมหานครเป็นศูนย์กลางการบริหารราชการแผ่นดินและนครใหญ่สุดของประเทศ และการปกครองส่วนภูมิภาค จัดระเบียบเป็น 76 จังหวัด แม้จะมีการสถาปนาระบอบราชาธิปไตยภายใต้รัฐธรรมนูญและประชาธิปไตยระบบรัฐสภาในปี 2475 แต่กองทัพยังมีบทบาทในการเมืองไทยสูง ล่าสุด เกิดรัฐประหารเมื่อวันที่ 22 พฤษภาคม 2557 และมีการปกครองแบบเผด็จการทหารนับแต่นั้น', 'พบหลักฐานการอยู่อาศั

#105 คำถามตั้งเอง 

In [0]:
cnt= 0
for i in dumps_117_qa[0]:
  if i['question'] != '':
    print (i['question'])
    cnt = cnt+1
print(cnt)

มูลนิธิวิกิมีเดียเป็นมูลนิธิประเภทใด
การเฝ้าสังเกตการณ์อีกแบบหนึ่งคือการสังเกตการณ์คลื่นอะไร
พันธุ์ทิพย์พลาซ่า นำลิฟท์แก้วมาติดตั้งเป็นแห่งที่เท่าไหร่ของประเทศไทย
นักคณิตศาสตร์มองว่าคณิตศาสตร์เป็นศาสตร์เชิงอะไร
การประมวลสารสนเทศสามารถมองเห็นได้ด้วยอะไร
ความหมายของการเมือง เป็นนิยามที่ได้รับการยอมรับอย่างสูงจากสำนักใด
ดิมมูบอร์เกียร์ ในช่วงก่อตั้งนั้นเล่นดนตรีแนวไหน
ปรัสเซียแตกหักกับราชวงศ์ใด
มหาวิทยาลัยใด ที่ผลิตบัณฑิตทางมานุษยวิทยาโดยตรง
คณะรัฐมนตรีได้ให้ความเห็นชอบการกู้เงินจากธนาคารเพื่อการพัฒนาอะไร
ภายหลังเหตุการณ์พฤษภาทมิฬ พลังของชนชั้นกลางเริ่มเข้ามามีบทบาทในอะไร
ปัญหาสะพานทั้งเจ็ดแห่งเมืองโคนิกส์เบิร์กเป็นจุดเริ่มต้นของทฤษฎีอะไร
การรู้จำแบบ มีจุดประสงค์ในเพื่อการจำแนก อะไร
ทฤษฎีข้อมูล แทนความหมายของอะไร
แนวคิดของซอฟต์แวร์ปรากฏครั้งแรกในเรียงความของใคร
สหราชอาณาจักรกับสหรัฐอเมริกาเป็นพันธมิตรกันช่วงสงครามอะไร
คอมพิวเตอร์วิทัศน์เป็นสาขาหนึ่งของวิทยาการอะไร
ขึดความสามารถของสแกนเนอร์ทีใช้นั้นสแกนได้กี่เส้นต่อนิ้ว
การประมวลผลภาพมีความหมายกับสัญญาณกี่มิติ
ชุดของภาพนิ่งเรียกว่าอะไร
แบบ

In [0]:
dumps_105_qa = dumps_117_qa[0][:]

In [0]:
path3 = '/content/drive/Team Drives/pre-snporject/data/sample_question'
open(path3+"dumps_wiki00_wiki01_106qa_json",'x',encoding = 'utf-8').write(json.dumps(dumps_105_qa))

2885444

#ผลลัพธ์ 106 คำถาม

In [0]:
for i in dumps_105_qa:
  data_content = ' '.join(i['text'])
  if(i['question']!=''):
    result = qa_fruit_demo(i['question'],data_content,3)
    i['content'] = data_content
    i['result'] = result
    print(i['question_id'])
    print(i['question'],i['result'])
    print("===================================================================================")

result_path = '/content/drive/Team Drives/pre-snporject/data/result'
open(path+"wikidump_106result_fruit_cosine",'x',encoding='utf-8').write(json.dumps(dumps_105_qa))
print("finish")


101
มูลนิธิวิกิมีเดียเป็นมูลนิธิประเภทใด {'choice_answer': {'ดำเนินการ', 'องค์กร'}, 'candidate': [7, 8, 9, 10, 11], 'neighbor': [9], 'neighbor_w_words': {'มูลนิธิวิกิมีเดีย': [9]}}


/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:101: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).


102
การเฝ้าสังเกตการณ์อีกแบบหนึ่งคือการสังเกตการณ์คลื่นอะไร {'choice_answer': {'ปรับปรุง', 'สุ่ม', 'ไฟฟ้า', 'คาด', 'กระจาย', 'อินฟราเรด', 'ลึก', 'วิธี', 'ถาวร', 'หัวข้อ', 'ดู', 'แหล่ง', 'เป้าหมาย', 'เมฆ', 'จำลอง', 'ซูเปอร์', 'รอบ', 'พอง', 'ถ่ายเท', 'ระบุ', 'โนวา', 'ดิจิตอล', 'สะท้อน', 'โน้มถ่วง', 'อนุภาคโฟตอน', 'ดำเนิน', 'โยงใย', 'มวล', 'อธิบาย', 'คาร์ล แจนสกี', 'ขนาด', 'หมวด', 'เวลา', 'เส้น', 'แลมบ์ดา', 'คอมพิวเตอร์', 'ระจุกดารา', 'วิวัฒนาการ', 'อัลตราไวโอเลต', 'แผ่', 'เครื่องมือ', 'บันทึก', 'สหพันธ์ดาราศาสตร์', 'รูป', 'เรือ', 'ตำแหน่ง', 'ฟิลเตอร์', 'วิชา', 'เดา', 'ยุค', 'บิกแบง', 'แกน', 'ดารากร', 'ฟิว', 'แผนที่', 'ขาว', 'คิดค้น', 'โคจร', 'กลาง', 'เชิง', 'ชะตากรรม', 'เพาะปลูก', 'ดวงดาว', 'ใกล้เคียง', 'มหาก', 'ปรากฏการณ์', 'โลก', 'ดวง', 'โทรทรรศน์', 'ข้อมูล', 'กำเนิด', 'รูปแบบ', 'ดาราจักรกัมมันต์', 'สำเร็จ', 'สลาย', 'ดาว', 'บุกเบิก', 'วัฒนธรรม', 'เอกภพ', 'ตัวอย่าง', 'วิจัย', '20', 'ปะทะ', 'ศึกษา', 'ปฏิเสธ', 'นิวตรอน', 'ปฏิทิน', 'บ่งบอก', 'คำนวณ', 'หอ', 'ติด', 'เจาะจง', 'สว่าง', 'ค้น', 

TypeError: ignored

In [0]:
dumps_105_qa[105]['question']

'คนเก่งทะลุโลก หรือ คนเก่งฟ้าประทาน แปลตรงตัวว่าอะไร'

In [0]:
for i in dumps_117_qa[0]:
  data_content = ' '.join(i['text'])
  result = qa_fruit_demo(i['question'],data_content,3)
  i['content'] = data_content
  i['result'] = result
  print(i['question_id'])
  print(i['question'],i['result'])
  print("===================================================================================")

result_path = '/content/drive/Team Drives/pre-snporject/data/result'
open(path+"wikidump_result_fruit_cosine",'x',encoding='utf-8').write(json.dumps(dumps_117_qa[0]))
print("finish")


101
มูลนิธิวิกิมีเดียเป็นมูลนิธิประเภทใด {'choice_answer': {'องค์กร', 'ดำเนินการ'}, 'candidate': [7, 8, 9, 10, 11], 'neighbor': [9]}


/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:101: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).


102
การเฝ้าสังเกตการณ์อีกแบบหนึ่งคือการสังเกตการณ์คลื่นอะไร {'choice_answer': {'20', 'ปฏิทิน', 'สังคม', 'หอ', 'ท้อง', 'กล้อง', 'ระบุ', 'หักเหแสง', 'ปฏิวัติ', 'วิทยาศาสตร์', 'ปะทะ', 'ต่ำ', 'หลักเกณฑ์', 'เปล่ง', 'ขยาย', 'ฟิว', 'วัตถุ', 'ดวงดาว', 'ดาวฤกษ์', 'ดิจิตอล', 'ปรับปรุง', 'ตรวจ', 'งาน', 'สลาย', 'สะท้อน', 'สิ้นสุด', 'สนับสนุน', 'นี้', 'สเปกตรัม', 'สมัคร', 'จำลอง', 'วิเคราะห์', 'ข้อมูล', 'ใกล้เคียง', 'โคจร', 'วัด', 'สำรวจ', 'อิเล็กตรอน', 'แกม', 'เรือ', 'เพาะปลูก', 'แตกต่าง', 'โทรทรรศน์', 'พอง', 'บ่งบอก', 'พลิก', 'สหประชาชาติ', 'ลำดับ', 'ประเภท', 'รอบ', 'แนว', 'ระบบ', 'จลนศาสตร์', 'แผ่', 'ขัดแย้ง', 'ชนิด', 'กำเนิด', 'สหพันธ์ดาราศาสตร์', 'เอกภพ', 'กระจาย', 'เสนอ', 'ดาว', 'ธรรมชาติ', 'เชิง', 'แหล่ง', 'ดู', 'ชะตากรรม', 'สุ่ม', 'สัญญาณ', 'ม่วง', 'แม่เหล็ก', 'สำเร็จ', 'แลมบ์ดา', 'ดาราศาสตร์', 'คิดค้น', 'ฟิสิกส์', 'อัลตราไวโอเลต', 'จดจำ', 'เดิม', 'มวล', 'แบ่ง', 'ศึกษา', 'ประกาศ', 'จักรวาล', 'วิวัฒนาการ', 'คณิตศาสตร์', 'คาด', 'คอมพิวเตอร์', 'วิชาวิทยาศาสตร์', 'ส่อง', 'วาด', 'วิจัย', 'กัมมัน

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:37: RuntimeWarning: invalid value encountered in double_scalars
/usr/local/lib/python3.6/dist-packages/numpy/core/_methods.py:135: RuntimeWarning: Degrees of freedom <= 0 for slice
  keepdims=keepdims)
/usr/local/lib/python3.6/dist-packages/numpy/core/_methods.py:105: RuntimeWarning: invalid value encountered in true_divide
  arrmean, rcount, out=arrmean, casting='unsafe', subok=False)
/usr/local/lib/python3.6/dist-packages/numpy/core/_methods.py:127: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


TypeError: ignored

In [0]:
result_path = '/content/drive/Team Drives/pre-snporject/data/result'
open(result_path+"test_create_file.txt",'x')
#open(result_path+"wikidump_106result_fruit_cosine_new",'w',encoding='utf-8').write(json.dumps(dumps_105_qa))
print("finish")

FileExistsError: ignored

In [0]:
type(dumps_117_qa[0])

list

In [0]:
type(dumps_105_qa)

list

In [0]:
result_path = '/content/drive/Team Drives/pre-snporject/result'
open(result_path+"wikidump_result_fruit_cosine_106qa",'x',encoding='utf-8').write(json.dumps(dumps_105_qa))

FileExistsError: ignored

In [0]:
cnt = 0
for i in dumps_117_qa[0]:
  if i['question'] == '':
    print (i['text'])
    print (i['id'])
    print (i['question_id'],i['question'])
   
    cnt = cnt + 1
print ("cnt",cnt)

['OS', 'OS, Os อาจหมายถึง']
789
147 
['โอเพนออฟฟิศดอตอ็อก', 'โอเพนออฟฟิศดอตอ็อก ( ย่อว่า OO.o หรือ OOo) เป็นชุดซอฟต์แวร์สำนักงานที่ทำงานบนหลายระบบปฏิบัติการ เผยแพร่ในรูปแบบซอฟต์แวร์เสรี เขียนขึ้นโดยใช้ชุดเครื่องมือส่วนต่อประสานกราฟิกของตัวเอง รองรับรูปแบบโอเพนด็อกคิวเมนต์ (ODF) ซึ่งเป็นมาตรฐานไอเอสโอ/ไออีซีเพื่อการแลกเปลี่ยนข้อมูล และใช้เป็นรูปแบบแฟ้มพื้นฐาน อีกทั้งยังรองรับรูปแบบเอกสารจากไมโครซอฟท์ ออฟฟิศ และอื่น ๆ กระทั่งเดือนพฤศจิกายน พ.ศ. 2552 โอเพนออฟฟิศดอตอ็อกรองรับมากกว่า 110 ภาษา ', 'โอเพนออฟฟิศดอตอ็อกพัฒนาต่อยอดมาจากสตาร์ออฟฟิศ (StarOffice) ซอฟต์แวร์สำนักงานจากสตาร์วิชัน (StarVision) ซึ่งภายหลังถูกควบกิจการโดยซัน ไมโครซิสเต็มส์ เมื่อเดือนสิงหาคม พ.ศ. 2542 รหัสต้นฉบับของชุดซอฟต์แวร์นี้เผยแพร่เมื่อเดือนกรกฎาคม พ.ศ. 2543 ด้วยจุดประสงค์เพื่อช่วงชิงส่วนแบ่งตลาดจากไมโครซอฟท์ ออฟฟิศ โดยเพิ่มทางเลือกเสรีต่อผู้ใช้และผู้พัฒนา รุ่นหลัง ๆ ของสตาร์ออฟฟิศจะใช้โอเพนออฟฟิศดอตอ็อกเป็นพื้นฐานแทน และเพิ่มองค์ประกอบที่เป็นกรรมสิทธิ์ของสตาร์ออฟฟิศ ', 'ซอฟต์แวร์และโครงการนี้อาจเรียกอย่างไม่เป็นทางก

In [0]:
  data_content = ' '.join(dumps_117_qa[0][46]['text'])
  result = qa_fruit_demo(dumps_117_qa[0][46]['question'],data_content,3)

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:37: RuntimeWarning: invalid value encountered in double_scalars
/usr/local/lib/python3.6/dist-packages/numpy/core/_methods.py:135: RuntimeWarning: Degrees of freedom <= 0 for slice
  keepdims=keepdims)
/usr/local/lib/python3.6/dist-packages/numpy/core/_methods.py:105: RuntimeWarning: invalid value encountered in true_divide
  arrmean, rcount, out=arrmean, casting='unsafe', subok=False)
/usr/local/lib/python3.6/dist-packages/numpy/core/_methods.py:127: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


TypeError: ignored

#position select

In [0]:
from pythainlp.tokenize import word_tokenize
from pythainlp.corpus import stopwords
from pythainlp import word_vector 
from gensim.models import Word2Vec
import pandas as pd
import numpy as np

words = stopwords.words('thai')

In [0]:
from google.colab import drive
drive.mount('/content/drive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=email%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdocs.test%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive.photos.readonly%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/drive


In [0]:
def qa_fruit1(question,paragraph):
  
  question_token = word_tokenize(question,engine= "deepcut") #question_token = ['เฮโจเกียว','หรือ','เฮเซเกียว','เป็น','เมือง','หลวง','ของ','ประเทศ','ใด']
  paragraph_token = word_tokenize(paragraph,engine= "deepcut")
  p_token = [w for w  in paragraph_token if w not in words and w not in ' ()|\?,:;/'] #คำ keyword ของพารากราฟ 
  q_token = [w for w  in question_token if w not in words and w not in ' ()|\?,:;/'] #คำ keyword ของคำถาม
  all_pos = keyword_n_position(p_token , question_token)
  np_pos = []
  set_d_nb = 3
  for i in all_pos[1]:
 
    for d_nb in range(set_d_nb):
        np_pos.append(i+d_nb)
        np_pos.append(i-d_nb)

  my_np_pos =  [pos for pos in np_pos if pos>0 and pos<len(p_token)]
  #check bug
  print ('p_tpken',p_token)
  print ('q_token',q_token)
  print ('all_pos',all_pos)
  print('set_d_nb',set_d_nb)
  print('my_np_pos',my_np_pos)
  print ('np_pos',np_pos)
  #p = np.array(all_pos[1])
  p = np.array(my_np_pos)
  treshold = p.sum()/len(p)+ p.std()
  print('threshol',treshold,all_pos[1])
  relavent_score = []
  for candidate in list(set(my_np_pos)):
    print('candidate',candidate,'tre',treshold)
    if candidate <= treshold :
      rs = 0 
      print ("candidate" ,candidate)
      for neighbor in all_pos[1]:
        if neighbor < treshold :
          tmp = candidate-neighbor
          if tmp <0 :
              tmp= -tmp
          rs = rs + tmp
          #rint("neighbor = ",neighbor,"tmp = ", tmp ,"rs = ",rs)
      relavent_score.append((candidate,rs))
  print (relavent_score)
  if len(relavent_score) == 0 :
    return [all_pos,cut_ans,relavent_score,[],[]]
  print ("find_max",find_max(relavent_score))
  answer = p_token[find_max(relavent_score)- 3:find_max(relavent_score)+3]
  print (relavent_score)
  return [all_pos,cut_ans,relavent_score,find_max,answer,threshold]





#Sol1 cut answerคือrelevant scoreที่เอาคำรอบข้าง(+-3)
  print (find_max(relavent_score))
  print ("answer= ",answer)
  choice_answer = []
  print ("cut answer = ",cut_ans(answer,q_token))


def keyword_n_position(p_token,question_token):
  nb = {}
  tk_list = []
  pos_list = []
  i = 0
  for tkn in p_token:
    if tkn in question_token and tkn not in tk_list:
      tk_list.append(tkn)
      pos_list.append(i)
      nb[tkn] = [i]
    elif tkn in question_token and tkn in  tk_list:
      nb[tkn].append(i)
      pos_list.append(i)
    i = i + 1 
  return (nb,pos_list)

def find_max(rs):
  if len(rs) == 0:
    return []
  m_max = 0
  i_max = 0
  for i in rs:
    if i[1] >= m_max:
      i_max = i
      m_max = i[1]
  return i_max[0]

def cut_ans(ans_tkn,q_token):
  return [i for i in ans_tkn if i not in q_token]

In [0]:
data = json.loads(open('/content/drive/Team Drives/pre-snporject/data/sample_data/nsc_100_qa_latest.json','r',encoding='utf-8').read())

In [0]:
data[-1].keys()

dict_keys(['question_id', 'question', 'answer', 'answer_begin_position ', 'answer_end_position', 'article_id', 'content', 'result', 'merge_content', 'cut_sym_content', 'cut_sym_content_w_sp', 'article'])

In [0]:
qa_fruit_position1 = data.copy()

for item in qa_fruit_position1:
  paragraph = item['cut_sym_content_w_sp']
  result =  qa_fruit1(item['question'],paragraph)
  item['result'] = result
  item['len_data'] = len(paragraph)
  item['top_n_answer'] = result[4]
  item['threshold'] = 
  

p_tpken ['เอเลี่ยน', 'ฝูง', 'มฤตยูนอก', 'โลก', 'เอเลียนส์', 'ภาพยนตร์', 'นิยาย', 'วิทยาศาสตร์แอคชั่น', 'ปี', 'ค', ' ศ', 'กำกับ', 'เจมส์ แคเมรอน', 'ภาพยนตร์', 'ปี', 'ค ศ', 'เอเลียน', 'สร้าง', 'ทเวนตีท์เซนจูรีฟอกซ์']
q_token ['เอเลียนส์', 'ภาพยนตร์', 'แนว']
all_pos ({'เอเลียนส์': [4], 'ภาพยนตร์': [5, 13]}, [4, 5, 13])
set_d_nb 3
my_np_pos [4, 4, 5, 3, 6, 2, 5, 5, 6, 4, 7, 3, 13, 13, 14, 12, 15, 11]
np_pos [4, 4, 5, 3, 6, 2, 5, 5, 6, 4, 7, 3, 13, 13, 14, 12, 15, 11]
threshol 11.56285918014984 [4, 5, 13]
candidate 2 tre 11.56285918014984
candidate 2
candidate 3 tre 11.56285918014984
candidate 3
candidate 4 tre 11.56285918014984
candidate 4
candidate 5 tre 11.56285918014984
candidate 5
candidate 6 tre 11.56285918014984
candidate 6
candidate 7 tre 11.56285918014984
candidate 7
candidate 11 tre 11.56285918014984
candidate 11
candidate 12 tre 11.56285918014984
candidate 13 tre 11.56285918014984
candidate 14 tre 11.56285918014984
candidate 15 tre 11.56285918014984
[(2, 5), (3, 3), (4, 1), (5, 1

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:26: RuntimeWarning: invalid value encountered in double_scalars
/usr/local/lib/python3.6/dist-packages/numpy/core/_methods.py:135: RuntimeWarning: Degrees of freedom <= 0 for slice
  keepdims=keepdims)
/usr/local/lib/python3.6/dist-packages/numpy/core/_methods.py:105: RuntimeWarning: invalid value encountered in true_divide
  arrmean, rcount, out=arrmean, casting='unsafe', subok=False)
/usr/local/lib/python3.6/dist-packages/numpy/core/_methods.py:127: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


p_tpken ['หม่อมเจ้ากฤษณาพักตรพิมล ศุขสวัสดิ', 'หม่อมเจ้ากฤษณาพักตรพิมล ศุขสวัสดิ', '  ดิศกุล', 'ธันวาคม', 'พระธิดา', 'สมเด็จพระเจ้าบรมวงศ์เธอ พระองค์เจ้าดิศวรกุมาร กรมพระยาดำรงราชานุภาพ', 'หม่อมแสง ดิศกุล ณ', 'อยุธยา', 'พระบรมวงศานุวงศ์', 'ลำดับ', 'ลำดับ', 'โปเจียม', 'ราชอาณาจักรไทย', 'พระประวัติ', 'พระประวัติ', 'หม่อมเจ้ากฤษณาพักตรพิมล', 'ท่าน', 'หญิงเพียน', 'ประสูติ', 'ธันวาคม', 'พ ศ', 'พระธิดา', 'สมเด็จพระเจ้าบรมวงศ์เธอ พระองค์เจ้าดิศวรกุมาร กรมพระยาดำรงราชานุภาพ', 'หม่อมแสง ดิศกุล ณ อยุธยา', 'ศตะรัต', 'พระราชนัดดา', 'พระบาทสมเด็จพระจอมเกล้าเจ้าอยู่หัว', 'หม่อมเจ้ากฤษณาพักตรพิมล', 'เชษฐา', 'เชษภคินี', 'อุทร', 'องค์', 'หม่อมเจ้ามารยาตรกัญญา ดิศกุล', 'เมษายน', 'พ', ' ศ', 'ธันวาคม', 'พ ศ', 'พรพิลาศ บุนนาค', 'ธันวาคม', 'พ ศ', 'ธันวาคม', 'พ ศ', 'หม่อมเจ้าพวง', 'มาศผกา ดิศกุล', 'กันยายน', 'พ', ' ศ', 'มิถุนายน', 'พ', ' ศ', 'หม่อมเจ้าศุกรวรรณดิศ ดิศกุล', 'มกราคม', 'พ ศ', 'กุมภาพันธ์', 'พ', ' ศ', 'หิณาวดี กำภู', 'พฤศจิกายน', 'พ', ' ศ', 'มีนาคม', 'พ ศ', 'ชีวิต', 'องค์', 'ชีวิต', 'องค์', 'หม่อ

In [0]:
qa_fruit_position1[-1]['result']['choice_answer']
qa_fruit_position1[-1].keys()

dict_keys(['question_id', 'question', 'answer', 'answer_begin_position ', 'answer_end_position', 'article_id', 'content', 'result', 'merge_content', 'cut_sym_content', 'cut_sym_content_w_sp', 'article'])

In [0]:
pd.DataFrame(qa_fruit_position1).to_csv('/content/drive/Team Drives/pre-snporject/result/qa_fruit_position1.csv', encoding='utf-8')
#open("/content/drive/Team Drives/pre-snporject/result/qa_fruit_position1.json",'w',encoding='utf-8').write(json.dumps(qa_fruit_position1))

In [0]:
qa_fruit_position1[7]['top_n_answer']

In [0]:
correct = [(8,3),(13,3),(15,3),(21,6),(23,4),(39,5),(40,5),(46,3),(47,3),(54,5),(60,4),(62,5),(71,3),(75,5),(84,3)]
len(correct)

15

ผลจากการหาคำตอบด้วยวิธีการพิจารณาจากตำแหน่ง กำหนดค่า threshold 
ด้วยวิธี qa_fruit1(question,paragraph) 

test data file = nsc_100_qa_latest.json

saved file = qa_fruit_position1.csv

โดยค่าพารากราฟนำเข้าจะทำการปรับให้แทนที่ตัวอักษร สัญลักษณ์อื่นๆที่ไม่ใช่ภาษาไทยแล้วตัวเลขด้วยช่องว่าง
ผลจากการใช้ค่าคะแนนสูงสุด และนำคำรอบข้างตำแหน่งที่มีคะแนนสูงสุดมาเป็นจำนวนทั้งสิ้น 6 คำ
ข้อที่สามารถดึงคำตอบมาได้ถูกต้องภายในคำทั้ง 6 มีดังนี้


correct = [(8,3),(13,3),(15,3),(21,6),(23,4),(39,5),(40,5),(46,3),(47,3),(54,5),(60,4),(62,5),(71,3),(75,5),(84,3)]

สรุป
สามารถเลือกคำตอบได้ถูกต้องทั้งหมด 15 ข้อ จาก 100 คำถาม
       
       โดยเป็นคำตอบที่มีคะแนนสูงสุด จำนวน 7 ข้อ จาก 100 คำถาม ค่าเฉลี่ยความยาวของพารากราฟ = 1723 จำนวนคำเฉลี่ย 385.14 คำ
       
       และเป็นคำที่อยู่รอบข้างคำที่เลือกอีกจำนวน 8 ข้อ จาก 100 คำถาม ค่าเฉลี่ยความยาวของพารากราฟ = 6470.5 จำนวนคำเฉลี่ย 1448.75 คำ
  
 ซึ่งจำนวนคำเฉลี่ยทั้ง 100 เอกสาร 734.69 คำ , ความยาวเฉลี่ยต่อเอกสาร 3144.90
โดย (เลขข้อ,ตำแหน่งของคำตอบ) ซึ่งตำแหน่งคำตอบสูงสุดจะอยู่ตรงกลาง นั่นคือ ตำแหน่งคำตอบ = 3 
และตำแหน่งอื่นๆคือคำรอบข้างที่ได้จากการ
เลือกคำตอบ 


ปัญหาของวิธีนี้ คือ จะไม่สามารถหาคำตอบได้เลย หากคำในคำถามไม่มีอยู่ในพารากราฟเนื้อหา 

กับปัญหาของ treshold ที่จะทำให้คำตอบที่อยู่นอกขอบเขตถูกตัดออกไป




In [0]:
summ = 0
cnt = 0
sum_c = 0
for i in qa_fruit_position1:
  summ = summ + len(word_tokenize(i['cut_sym_content_w_sp']))
  sum_c += len(i['cut_sym_content_w_sp'])
  cnt = cnt+1
print (sum_c/cnt ,summ/cnt)

3144.9 734.69


In [0]:
# top_5 = [(8,3),(13,3),(15,3),(21,6),(23,4),(39,5),(40,5),(46,3),(47,3),(54,5),(60,4),(62,5),(71,3),(75,5),(84,3)]
# summ = 0
# cnt = 0
# for i in top_5:
#   if i[1] != 3:
#     summ = summ + len(word_tokenize(qa_fruit_position1[i[0]]['cut_sym_content_w_sp']))
#     cnt= cnt+1
    
# print(summ)
# print(cnt)
# print(summ/cnt)

11590
8
1448.75


In [0]:
qa_fruit_position1[-1].keys()


dict_keys(['question_id', 'question', 'answer', 'answer_begin_position ', 'answer_end_position', 'article_id', 'content', 'result', 'merge_content', 'cut_sym_content', 'cut_sym_content_w_sp', 'article', 'len_data', 'top_n_answer'])

In [0]:
pd.DataFrame(qa_fruit_position1)[['answer','top_n_answer','len_data']]
top_5 = [(8,3),(13,3),(15,3),(21,6),(23,4),(39,5),(40,5),(46,3),(47,3),(54,5),(60,4),(62,5),(71,3),(75,5),(84,3)]


answer  \
0                             นิยายวิทยาศาสตร์แอคชั่น   
1                                    ราชวงศ์กาเปเตียง   
2                                           องค์ชาย 8   
3                                           สวัสดิกุล   
4                                           ไม้ยืนต้น   
5   ลูกทั้งสองเจริญมาจากไซโกตเดียวแล้วจึงแยกและสร้...   
6                                          ฟิลิปปินส์   
7             สมเด็จพระราชินีนาถอีซาเบลที่ 2 แห่งสเปน   
8                                        รัก โรแมนติก   
9                                   คหกรรมและศิลปกรรม   
10                                   หม่อมเจ้าสุทัศน์   
11                             29 พฤศจิกายน ค.ศ. 1976   
12  พระเจ้าบรมวงศ์เธอ พระองค์เจ้าศุขสวัสดี กรมหลวง...   
13                                      ประเทศญี่ปุ่น   
14                        วันที่ 28 กรกฎาคม ค.ศ. 1951   
15                                        เมืองอิทาคา   
16                                      จังหวัดลพบุรี   
17                                           พาราโบลา   
18                                  ภูสิษฐ์ เอี่ยมสุข   
19                              Utip Freshy Idol 2007   
20                                  เดือนกันยายน 2550   
21                               สโมสรฟุตบอลอาร์เซนอล   
22                                          พ.ศ. 2553   
23                                 คารีสา สปริงเก็ตต์   
24                                          ทากามัตสึ   
25                             มหาวิทยาลัยเกษตรศาสตร์   
26                                       สวีตตี้เบลล์   
27                 นางสาวคลอทิลด์ มารี ปาสคาลล์ คูโร่   
28                                                ยอด   
29                                       เทพ ประทานพร   
..                                                ...   
70                              เดือนตุลาคม ค.ศ. 1958   
71                                        อเมริกากลาง   
72                                       ๒ ปี ๖ เดือน   
73  รัฐมนตรีว่าการกระทรวงทรัพยากรธรรมชาติและสิ่งแว...   
74                               240 ล้านดอลลาร์สหรัฐ   
75                                          งานธนาคาร   
76                                 พระเจ้ายอดเชียงราย   
77                                            สองสมัย   
78                                          ค.ศ. 2006   
79                               พระชนมพรรษา 13 พรรษา   
80                                     เคย์โกะ โอยามา   
81                                                  5   
82                                          ทางช่อง 3   
83                                        พจน์ อานนท์   
84                                         เกาะซามาร์   
85                                          พ.ศ. 2548   
86                                     ประเทศฝรั่งเศส   
87                                        แพรเยื่อไม้   
88                                        จังหวัดตรัง   
89                          หม่อมหลวงอภิรัฐ จรูญโรจน์   
90                             ลูกน้ำ นางงามเลสเบี้ยน   
91                                             6 แห่ง   
92                                       จังหวัดลำพูน   
93                                         ไวลด์วันส์   
94  โอลิเวอร์ เรจินัลด์ แทมโบ (Oliver Reginald Tambo)   
95                          นางจารุวรรณ ชัยจิตวณิชกุล   
96                               นายพรเทพ เตชะไพบูลย์   
97                            นายณัฐพร จาตุศรีพิทักษ์   
98                                           ทนายความ   
99                                  แควใหญ่และแควน้อย   

                                         top_n_answer  len_data  
0         [ปี, ค,  ศ, กำกับ, เจมส์ แคเมรอน, ภาพยนตร์]       290  
1   [ดยุก, บูร์กอญ, พระราชสมภพ, พระราชบิดา, เคานต์...      1002  
2   [เฝิง, เส้าเฟิง, ลูก, ชาย, หัวแก้วหัวแหวน, ธุร...      1143  
3                [สกุล, เดิม, ระนอง, มิถุนายน, พ,  ศ]      1684  
4         [ไม้, ชิงชัน, ลักษณะ, แข็ง, เหนียว, ลักษณะ]       836  
5                   [เจริญ, ไข่, สอง, ใบ, ผสม, เซลล์]       479  
6                 [กำนันเสือ, ลูก, สาว, คน, ผ่า, โ

In [0]:
pd.DataFrame(qa_fruit_position1)[['answer','top_n_answer','len_data']][29:70]
#(39,5),(40,5),(46,3),(47,3),(54,5),(60,4),(62,5),()

answer  \
29                                       เทพ ประทานพร   
30                                          พ.ศ. 2501   
31                                           ค.ศ.1947   
32                                 มหาวิทยาโคเปนเฮเกน   
33                                   เจตริน วรรธนะสิน   
34  ราชสถาบันสถาปนิกอังกฤษ (Royal Institute of Bri...   
35                        สหพันธ์สาธารณรัฐอเมริกากลาง   
36                                      สภาเกาะนาอูรู   
37                                 ตำแหน่ง พอยท์การ์ด   
38                                 ปรียานุช ปานประดับ   
39                                         ชาวอียิปต์   
40                                          ทวีปยุโรป   
41                                        บุปผา สายชล   
42                                นายทวิช กลิ่นประทุม   
43                        วันที่ 20 พฤษภาคม ค.ศ. 2016   
44                                     ประเทศโปรตุเกส   
45                                              อีสาน   
46                               ปาณรวัฐ กิตติกรเจริญ   
47                          นางปิยวรา ทีขะระ เนตรน้อย   
48                                             OV-099   
49                              10 มิถุนายน พ.ศ. 2539   
50                                                 14   
51                                     พระเจ้าเล่าปี่   
52                     ทันตแพทย์หญิง รัตนาวดี ทองเล็ก   
53                                            โปแลนด์   
54                             เอเชียตะวันออกเฉียงใต้   
55                                     แม่น้ำพรหมบุตร   
56                                         ภาษาอังกฤษ   
57                               เบอร์ - มนตรี ศิริชู   
58                         พระเจ้าหงสาวดีรัชกาลที่ 14   
59                                      อาคม ปรีดากุล   
60                                         เอ็กเบิร์ต   
61                                   จังหวัดอุตรดิตถ์   
62                                สุจาริณี วิวัชรวงศ์   
63                    ดินดอนสามเหลี่ยมปากแม่น้ำอิรวดี   
64                                    จาเร็ด คัชเนอร์   
65             Photographs: Annie Leibovitz 1970-1990   
66                              หม่อมเจ้าภีศเดช รัชนี   
67                                          จิวแป๊ะทง   
68                คณะนิติศาสตร์ จุฬาลงกรณ์มหาวิทยาลัย   
69                                  รัดเกล้า อามระดิษ   

                                         top_n_answer  len_data  
29              [วงการ, แดง, ฉาย, แวว, ร้อง, เด่นชัด]      1005  
30              [ภาพยนตร์, ฉาย, กวาด, หลัก, ล้าน, ทำ]      2048  
31                                                 []      2373  
32                                                 []      1811  
33  [นับถือ, ศาสนา, พุทธ, รีตนิกาย, โปรเตสแตนต์, ส...      1458  
34                                                 []      1110  
35            [หมาย, เจตจำนง, แรง, กล้า, กัวเตมา, ลา]      1340  
36                                                 []     13560  
37            [ฉายา, แมจิก, สมควร, ขนาน, นาม, ควบคุม]      1670  
38  [พุดกรอง วิบูลย์สิน ช่อง, คน, โลก, บท, คลเมขลา...      4132  
39  [คริสตกาล, ทาอีส, บุญ, บุญ, อียิปต์, คริสต์ศตว...       491  
40  [เดนมาร์ก, ภาษา, เยอรมัน, คาบสมุทร, ทวีปยุโรป,...       259  
41                                                 []      1091  
42           [กลิ่น, ประทุม, ชื่อ, เล่น, เอมี่, ชื่อ]      5559  
43     [ทำ, สตรี, คน, สมัคร, เลือกตั้ง, ประธานาธิบดี]      2396  
44                                                 []       401  
45                                                 []       273  
46  [บท, ประพันธ์, ปาณรวัฐ,  กิตติกรเจริญ, สร้าง, ...       362  
47  [นางปิยวรา ที, ขะระ, เนตรน้อย, ถวาย, งาน, สมเด...      1253  
48            [ฐาน, ปล่อย, จรวด, ยาน, จรวด, บูสเตอร์]      1747  
49              [ขา, หมู, ภาพยนตร์, เล่า, ชาย, หนุ่ม]       780  
50           [ออกอากาศ, เพลง, ละคร, เพลง, ละคร, เพลง]       944  
51                                                 []      3445  
52                                                 []      4237  
53

In [0]:
qa_fruit_position1[32]

{'answer': 'มหาวิทยาโคเปนเฮเกน',
 'answer_begin_position ': 427,
 'answer_end_position': 445,
 'article': 'ฮันส์ คริสเทียน เออร์สเตด',
 'article_id': 156628,
 'content': '<doc id="156628" url="https://th.wikipedia.org/wiki?curid=156628" title="ฮันส์ คริสเทียน เออร์สเตด">ฮันส์ คริสเทียน เออร์สเตด ฮันส์ คริสเทียน เออร์สเตด (Hans Christian Ørsted, 14 สิงหาคม พ.ศ. 2320 - 9 มีนาคม พ.ศ. 2394) เป็นนักฟิสิกส์และนักเคมีชาวเดสัมพันธ์ระหว่างไฟฟ้าและความเป็นแม่เหล็ก หรือที่เรียกว่า ทฤษฎีแม่เหล็กไฟฟ้า ฮานส์ คริสเตียน เออร์สเตด ) เกิดเมื่อวันที่ 14 สิงหาคม พ.ศ. 2320 เขาเป็นศาสตราจารย์ภาควิชาฟิสิกส์ ประจำมหาวิทยาโคเปนเฮเกน ประเทศเดนมาร์ก เออร์สเตดค้นพบความสัมพันธ์ระหว่างไฟฟ้าและสนามแม่เหล็กด้วยความบังเอิญ ในเดือนเมษายน ปี พ.ศ. 2363 ขณะบรรยายวิชาฟิสิกส์ในหัวข้อ คุณสมบัติของกระแสไฟฟ้า (Electricity, Galvanism and Magnetism) โดยมีอุปกรณ์ในการทำการทดลองประกอบการบรรยาย คือ แบตเตอรี่ สายไฟ และเข็มทิศ เออร์สเตดได้ทำการทดลองเกี่ยวกับปรากฏการณ์ที่เข็มทิศจะเบนเมื่อมีฝนตกหนัก และฟ้าแลบ เพื่อลองดูว่าจะเกิดอะไรขึ้

In [0]:
qa_fruit_position1[41]

{'answer': 'บุปผา สายชล',
 'answer_begin_position ': 521,
 'answer_end_position': 532,
 'article': 'เก่งกาจ จงใจพระ',
 'article_id': 130642,
 'content': '<doc id="130642" url="https://th.wikipedia.org/wiki?curid=130642" title="เก่งกาจ จงใจพระ">เก่งกาจ จงใจพระ เก่งกาจ จงใจพระ เดิมมีชื่อว่า ศรีไพร ใจพระ เกิดเมื่อวันที่ 16 ตุลาคม พ.ศ. 2481 ที่ตำบลศาลเจ้าโรงทอง อำเภอวิเศษชัยชาญ จังหวัดอ่างทอง ในครอบครัวคนไทยเชื้อสายจีน ในอดีตเคยเป็นดาราภาพยนตร์ ผู้กำกับภาพยนตร์ นักจัดรายการวิทยุ นักร้องเพลงลูกทุ่ง และผู้จัดการวงดนตรีลูกทุ่ง โดยผลงานการแสดงที่เด่น ๆ ได้แก่ การรับบท ไอ้แว่น เพื่อนรักของ ไอ้คล้าว ในภาพยนตร์เรื่อง มนต์รักลูกทุ่ง ในปี พ.ศ. 2513 โดยแสดงคู่กับมิตร ชัยบัญชา และบุปผา สายชล ที่ต่อมากลายเป็นภรรยาของตนเอง ต่อมา ได้เปลี่ยนชื่อ และนามสกุล และศึกษาโหราศาสตร์มาตั้งแต่เด็ก จนกลายเป็นหมอดูชื่อดัง โดยมักจะให้คำทำนายเกี่ยวกับสถานการณ์บ้านเมืองตามสื่อมวลชนเป็นระยะ ๆ โดยเริ่มงานครั้งแรกด้วยการเป็นคอลัมนิสต์โหรการเมืองในหนังสือพิมพ์เดลินิวส์ ในปี พ.ศ. 2518 เคยเป็นพิธีกรในรายการ "นายมั่ง นายคง คน